# Deploy a custom application with Pulumi

This notebook outlines how to use Pulumi to deploy a custom application.

## Initialize the environment

Start the environment and import the DataRobot library. Before proceeding, [download the necessary assets](https://datarobot-doc-assets.s3.us-east-1.amazonaws.com/deploy_custom_app.zip) to execute the tasks in this notebook.

In [1]:
import os
import datarobot as dr

os.environ['PULUMI_CONFIG_PASSPHRASE'] = 'default'

assert 'DATAROBOT_API_TOKEN' in os.environ, 'Please set the DATAROBOT_API_TOKEN environment variable'
assert 'DATAROBOT_ENDPOINT' in os.environ, 'Please set the DATAROBOT_ENDPOINT environment variable'

dr.Client()

## Set up a project

Set up functions to create and build or destroy your Pulumi stack.

In [2]:
from pulumi import automation as auto


def stack_up(project_name: str, stack_name: str, program: callable) -> auto.Stack:
    # create (or select if one already exists) a stack that uses our inline program
    stack = auto.create_or_select_stack(
        stack_name=stack_name, project_name=project_name, program=program
    )

    stack.refresh(on_output=print)

    stack.up(on_output=print)
    return stack


def destroy_project(stack: auto.Stack):
    """Destroy pulumi project"""
    stack_name = stack.name
    stack.destroy(on_output=print)

    stack.workspace.remove_stack(stack_name)
    print(f"stack {stack_name} in project removed")

## Create a declarative custom application deployment

Use this cell to create a custom application deployment. Add your source code to DataRobot and then initialize the application. The `make_custom_application` function below shows how to declaratively do this. You'll see some variant of this across all application templates.

In [3]:
import pulumi_datarobot as datarobot
import pulumi


def make_custom_application():
    """Make a custom app on DataRobot.

    Upload source code to create source. Then initialize application.
    """

    file_mapping = [
        ("frontend/app.py", "app.py"),
        ("frontend/requirements.txt", "requirements.txt"),
        ("frontend/start-app.sh", "start-app.sh"),
    ]

    app_source = datarobot.ApplicationSource(
        resource_name="App Template Minis - Custom App Source",
        files=file_mapping,
        base_environment_id="6542cd582a9d3d51bf4ac71e",  # Python 3.9 streamlit environment
    )

    app = datarobot.CustomApplication(
        resource_name="App Template Minis - Custom App",
        source_version_id=app_source.version_id,
    )
    pulumi.export("Application Source Id", app_source.id)
    pulumi.export("Application Id", app.id)
    pulumi.export("Application Url", app.application_url)

## Run the Pulumi stack

You can now run the Pulumi stack. Doing so takes the files in the `frontend` directory from the downloaded assets, puts them into DataRobot, and initializes the application.

In [ ]:
project_name = "AppTemplateMinis-CustomApplications"
stack_name = "MarshallsCustomApplicationDeployer"

stack = stack_up(project_name, stack_name, program=make_custom_application)

### Interact with outputs

In [ ]:
import webbrowser

outputs = stack.outputs()
app_url = outputs.get("Application Url").value
webbrowser.open(app_url)

## Clear your work

You may not be interested in keeping the application. Use this cell to shut down the stack, deleting any assets created in DataRobot.

In [ ]:
destroy_project(stack)